In [9]:
import pdfplumber
import re
import os
import pandas as pd
import matplotlib.pyplot as plt
import pyecharts.options as opts
from pyecharts.charts import Line, Page


In [10]:
def get_pdf_info(pdf_name):
    content = ""

    with pdfplumber.open(pdf_name) as pdf:
        for n in range(0, 40):
            page = pdf.pages[n]
            text = page.extract_text()
            if text != None:
                content += text
            else:
                pass

    contentClear = content.replace("\n", "")
    content2 = re.findall("公司简介和主要财务指标(.*?)公司业务概要", contentClear, re.S)[1]

    indexName = ["股票简称", "股票代码", "公司的法定代表人", "办公地址", "公司国际互联网网址", "电子信箱"]
    indexName2 = ["股票代码", "公司的中文名称", "注册地址", "办公地址的邮政编码", "电子信箱", "二、联系人和联系方式"]

    info = []

    for i in range(len(indexName)):
        strRes = str(indexName[i]) + "(.*?)" + str(indexName2[i])
        v = re.findall(strRes, content2, re.S)[0].replace("\n", "").strip()
        info.append(v)

    mainInfo = info[0:1] + [str(info[1])[0:7]] + info[2:]
    strRes2 = re.findall("五、主要会计数据和财务指标(.*?)六、分季度主要财务指标", content2, re.S)[0]
    strRes3 = re.findall("营业收入（元）(.*?)归属于上市公司股东的净利", strRes2, re.S)[0]
    strRes4 = re.sub(r"-?\d+(?:,\d{1,3})*(?:\.\d+)*%", "", strRes3)
    v2 = re.findall(r"-?\d+(?:,\d{1,3})*(?:\.\d+)*", strRes4)

    if len(v2) == 3:
        for one in v2:
            mainInfo.append(one)
    else:
        for one in v2[::2]:
            mainInfo.append(one)

    return mainInfo

def getDir(filePath):
    filesList = []
    pathInfo = os.walk(filePath)
    for root, dirs, files in pathInfo:
        for file in files:
            if os.path.splitext(file)[1] == ".pdf":
                filesList.append(os.path.join(root, file))
    return filesList

In [11]:
indexList = ["股票简称", "股票代码", "法定代表人", "办公地址", "公司网址", "电子信箱", "2019年", "2018年", "2017年"]
data = []
for name in getDir("C:/Users/XY/Desktop/2019")[0:20]:
    data.append(get_pdf_info(name))
df = pd.DataFrame(data=data, columns=indexList)

In [12]:
df

股票简称    股票代码 法定代表人                                      办公地址  \
0   恒信东方  300081   孟宪民                     北京市海淀区蓝靛厂南路牛顿办公区北区11层   
1   华中数控  300161   陈吉红                             武汉市东湖开发区华工科技园   
2   天晟新材  300169   吴海宙                             常州市龙锦路 号  508   
3   元力股份  300174   许文显                           福建省南平市陈坑至瓦口工业园区   
4   日科化学  300214   彭国锋                            山东省昌乐县英轩街3999号   
5   方直科技  300235   黄元忠                     深圳市南山区大新路198号创新大厦B座9楼   
6   华录百纳  300291    方刚                         北京市朝阳区安家楼50号院A7-2   
7   晶盛机电  300316   曹建伟                      浙江省杭州市余杭区五常街道创智一号2号楼   
8   博腾股份  300363   居年丰  重庆市北碚区水土园区方正大道重庆博腾制药科技股份有限公司新药外包服务基地研发中心   
9   安控科技  300370   许永良                           北京市海淀区地锦路9号院6号楼   
10  四通新材  300428   臧立国                            保定市清苑区发展西街359号   
11   普丽盛  300442   姜卫东                          上海市金山区张堰镇金张支路84号   
12  创业慧康  300451    葛航                  杭州市滨江区长河街道越达巷92号创业智慧大厦五楼   
13  惠伦晶体  300460   赵积清                         广东省东莞市黄江镇黄江东环路68号   
14  山鼎设计  300492    陈栗                    成都市锦江区东大街芷泉段6号1栋1单元37层   
15   新易盛  300502   高光荣                         成都市双流区公兴镇物联西街127号   
16  天邑股份  300504   李世宏                       四川省大邑县晋原镇雪山大道一段198号   
17   川金诺  300505    刘甍                      云南省昆明市呈贡区上海东盟大厦A座10楼   
18  新光药业  300519   王岳钧                         浙江省嵊州市剡湖街道环城西路25号   
19  幸福蓝海  300528   蒋小平                            南京市栖霞区元化路8号28幢   

                           公司网址                         电子信箱  \
0         http://www.hxgro.com/             office@hxgro.com   
1           www.huazhongcnc.com               hcnc@hzncc.com   
2        http://www.tschina.com           dongmi@tschina.com   
3          www.yuanlicarbon.com          dm@yuanlicarbon.com   
4       http://www.rikechem.com        rikechem@rikechem.com   
5            www.kingsunedu.com  kingsunsoft@kingsunsoft.com   
6           http://www.hlbn.cc/               hbndsh@hlbn.cc   
7           http://www.jsjd.cc/                 jsjd@jsjd.cc   
8          http://www.porton.cn          porton.db@porton.cn   
9                 www.etrol.com               info@etrol.com   
10       http://www.stnm.com.cn             info@stnm.com.cn   
11               www.cn-pls.com               pls@cn-pls.com   
12    https://www.bsoft.com.cn/           bsoft@bsoft.com.cn   
13        http://www.dgylec.com                yl@dgylec.com   
14  http://www.cendes-arch.com/   cendes.bso@cendes-arch.com   
15            www.eoptolink.com             ir@eoptolink.com   
16             www.tianyisc.com            tykh@tianyisc.com   
17       http://www.cjnphos.com              cjncc61@163.com   
18     http:// www.xgpharma.com             xgpharma@163.com   
19       http://www.omnijoi.com            board@omnijoi.com   

               2019年             2018年             2017年  
0     546,414,932.58    697,723,347.65    414,396,876.31  
1     906,039,496.44    819,575,843.82    985,192,133.80  
2     893,508,335.61    904,549,750.64    772,336,483.85  
3   1,281,614,548.23  1,701,701,972.82    853,321,121.35  
4   2,420,120,333.77  1,568,771,296.29  2,103,216,856.38  
5     109,014,398.01    107,245,103.63    100,510,607.42  
6     611,431,097.94    629,521,249.35  2,247,623,728.70  
7   3,109,742,819.15  2,535,711,475.03  1,948,848,200.36  
8   1,551,298,762.27  1,184,863,256.32  1,184,088,767.29  
9   1,255,875,227.80  1,371,045,013.22  1,766,370,972.14  
10  6,426,889,811.08  6,754,637,522.85  6,262,823,276.54  
11    640,060,243.46    579,549,995.56    694,225,978.93  
12  1,479,824,747.66  1,290,288,361.43  1,152,952,938.09  
13    309,942,731.09    318,987,012.27    363,278,187.71  
14    213,738,816.56    215,946,744.36    149,941,000.43  
15  1,164,873,682.36    759,950,284.50    877,365,361.78  
16  2,137,738,779.11  2,775,005,851.17  2,354,874,134.30  
17  1,125,995,638.52    965,593,161.31    799,813,584.75  
18    291,262,099.70    276,257,365.69    310,865,113.13  
19  2,138,087,936.10  1,654,823,836.35  1,517,230,

# 加载模块 pip install pyecharts

In [13]:

page = Page()
x = ["2019年", "2018年", "2017年"]

for row in data:
    y = [float(row[-3].replace(",", "")), float(row[-2].replace(",", "")), float(row[-1].replace(",", ""))]
    line = Line()
    line.add_xaxis(x)
    line.add_yaxis(str(row[0]) + ":" + str(row[1]), y, is_connect_nones=True)
    line.set_global_opts(title_opts=opts.TitleOpts(title="近三年营业收入（元）"))
    page.add(line)
page.render_notebook()


# 分析

 从图中可以看出,少数企业在2017年到2018年营业收入稳步增长或稳步下降，大多数企业营业收入在2018年经历了较大改变，要么出现大增长，要么出现大下跌。说明企业经营存在较大的不稳定性。营业收入变化可能会造成股价变动，可结合公司股价分析营业收入对股价的影响。
